# BeleBele Benchmark Dataset

- Meta's multilingual multiple choice reading comprehension dataset (Multiple Choice QA) based on FLORES
- Paper: https://arxiv.org/pdf/2308.16884


In [9]:
!pip install -q datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.1/542.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.7 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires requests==2.31.0, but you have requests 2.32.3 which is incompatible.


In [10]:
# a lot of these came from the evaluation script so there are some that are unnecessary
from datasets import load_dataset, get_dataset_config_names, Dataset
import random
import numpy as np
import torch
import torch.nn.functional as F
from transformers import AutoModelForSequenceClassification, AutoTokenizer
from torch.utils.data import DataLoader
import pandas as pd
from datasets import Dataset
from sklearn.utils import resample
from sklearn.utils import resample
from copy import copy
from torch.utils.data import DataLoader
import argparse
from tqdm import tqdm

In [4]:
import requests
# headers = {"Authorization": f"Bearer {API_TOKEN}"}
API_URL = "https://datasets-server.huggingface.co/splits?dataset=facebook/belebele"
def query():
    response = requests.get(API_URL)
    return response.json()
data = query()

In [5]:
data

{'splits': [{'dataset': 'facebook/belebele',
   'config': 'default',
   'split': 'acm_Arab'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'arz_Arab'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'ceb_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'fin_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'hin_Deva'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'ita_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'khm_Khmr'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'lvs_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'npi_Deva'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'pol_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'slv_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'default', 'split': 'swe_Latn'},
  {'dataset': 'facebook/belebele', 'config': 'de

In [6]:
langs = []
for row in data['splits']:
  langs.append(row['split'])

In [16]:
print(langs)

['acm_Arab', 'arz_Arab', 'ceb_Latn', 'fin_Latn', 'hin_Deva', 'ita_Latn', 'khm_Khmr', 'lvs_Latn', 'npi_Deva', 'pol_Latn', 'slv_Latn', 'swe_Latn', 'tso_Latn', 'xho_Latn', 'afr_Latn', 'asm_Beng', 'ces_Latn', 'fra_Latn', 'hin_Latn', 'jav_Latn', 'kin_Latn', 'mal_Mlym', 'npi_Latn', 'por_Latn', 'sna_Latn', 'swh_Latn', 'tur_Latn', 'yor_Latn', 'als_Latn', 'azj_Latn', 'ckb_Arab', 'fuv_Latn', 'hrv_Latn', 'jpn_Jpan', 'kir_Cyrl', 'mar_Deva', 'nso_Latn', 'snd_Arab', 'tam_Taml', 'ukr_Cyrl', 'zho_Hans', 'amh_Ethi', 'bam_Latn', 'dan_Latn', 'gaz_Latn', 'hun_Latn', 'kac_Latn', 'kor_Hang', 'mkd_Cyrl', 'nya_Latn', 'ron_Latn', 'som_Latn', 'tel_Telu', 'urd_Arab', 'zho_Hant', 'apc_Arab', 'ben_Beng', 'deu_Latn', 'grn_Latn', 'hye_Armn', 'kan_Knda', 'lao_Laoo', 'mlt_Latn', 'ory_Orya', 'rus_Cyrl', 'sot_Latn', 'tgk_Cyrl', 'urd_Latn', 'zsm_Latn', 'arb_Arab', 'ben_Latn', 'ell_Grek', 'guj_Gujr', 'ibo_Latn', 'kat_Geor', 'lin_Latn', 'mri_Latn', 'pan_Guru', 'shn_Mymr', 'spa_Latn', 'tgl_Latn', 'uzn_Latn', 'zul_Latn', 'ar

In [17]:
def fill_template(templates, values):
    temp = random.sample(templates,1)[0]
    for i in range(len(values)):
        #print(f"i: {i}, values: {values[i]}")
        temp = temp.replace("${"+str(i+1)+"}", values[i])
    return temp

In [23]:
# This processes 192 languages * 900 rows for each language so it's taking a while...
print("Processing Belebele...")
dataset_name = "facebook/belebele"
templates = ["Passage: \"${1}\"\n Question: \"${2}\"\n Answer: \"${3}\"",
             "\"${1}\"\n According to the passage above, the answer of \"${2}\" is \"${3}\"",
             "Passage: \"${1}\"\n Question: \"${2}\"\n Answer: \"${3}\"",
             "\"${1}\"\n Q: \"${2}\"\n A: \"${3}\"",
             "\"${1}\" \"${2}\" \"${3}\""]
label_column = 'answers'
question='context'
choices=['answers']

belebele_statements = {lang:[] for lang in langs}
for lang in tqdm(langs):
  #print(f"Processing {lang}...")

  data = load_dataset(dataset_name, split=lang)

  for row in data:
    statement_row = {}
    right_answer = row['correct_answer_num']

    # Choose from templates given
    temp = random.choice(templates)

    # choose between 1 and 0
    truth_val = random.choice(range(0, 2))

    if truth_val:
      idx = right_answer
    else:
      idx = random.choice([i for i in range(1, 5) if i != right_answer])

    statement_row['is_true'] = 1 if idx == right_answer else 0
    values = []
    values.append(row['flores_passage'])
    values.append(row['question'])
    values.append(row[f'mc_answer{idx}'])
    statement_row['statement'] = fill_template([temp], values)

    belebele_statements[lang].append(statement_row)
    #print(statement_row)

#belebele_statements, belebele_langs = generate_eval_belebele(dataset, templates)

Processing Belebele...
Processing acm_Arab...
Processing arz_Arab...
Processing ceb_Latn...
Processing fin_Latn...
Processing hin_Deva...
Processing ita_Latn...
Processing khm_Khmr...
Processing lvs_Latn...
Processing npi_Deva...
Processing pol_Latn...
Processing slv_Latn...
Processing swe_Latn...
Processing tso_Latn...
Processing xho_Latn...
Processing afr_Latn...
Processing asm_Beng...
Processing ces_Latn...
Processing fra_Latn...
Processing hin_Latn...
Processing jav_Latn...
Processing kin_Latn...
Processing mal_Mlym...
Processing npi_Latn...
Processing por_Latn...
Processing sna_Latn...
Processing swh_Latn...
Processing tur_Latn...
Processing yor_Latn...
Processing als_Latn...
Processing azj_Latn...
Processing ckb_Arab...
Processing fuv_Latn...
Processing hrv_Latn...
Processing jpn_Jpan...
Processing kir_Cyrl...
Processing mar_Deva...
Processing nso_Latn...
Processing snd_Arab...
Processing tam_Taml...
Processing ukr_Cyrl...
Processing zho_Hans...
Processing amh_Ethi...
Processing 

In [24]:
belebele_statements['kor_Hang'][0]

{'is_true': 1,
 'statement': '"2차 세계 대전에서 독일은 공통의 적이었고 이는 소련과 미국의 협력으로 이어졌습니다. 전쟁이 끝남과 함께 시스템, 변화 및 문화의 충돌은 여러 국가의 쇠락으로 이어졌습니다. 종전 2년이라는 세월이 흐르면서 이전의 동맹국들은 이제 적이 되었고 냉전이 시작되었다. 냉전은 이후 40년 동안 지속될 것이었고 아프리카에서 아시아 지역, 아프가니스탄, 쿠바, 그리고 다른 많은 지역의 전장에서 대리군들에 의한 실제 싸움이 될 것이었다."\n Q: "지문에 따르면, 다음 중 소련과 미국 간의 관계에 영향을 미치지 않은 것은 무엇인가?"\n A: "독일에 대한 의견"'}

In [28]:
def push_dataset(statements, langs, dataset_name):
  for lang_code in langs:
    print(f"Processing {lang_code}...")
    #statements[lang_code].push_to_hub(f"mbzuai-ugrip-statement-tuning/{dataset_name}", lang_code, split='train')
    ds = Dataset.from_list(statements[lang_code])
    ds.push_to_hub(f"mbzuai-ugrip-statement-tuning/{dataset_name}", lang_code, split='train')

In [30]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) n
Token is valid (permission: write).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [31]:
push_dataset(belebele_statements, langs, "belebele")

Processing acm_Arab...


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Processing arz_Arab...


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

...

README.md:   0%|          | 0.00/37.1k [00:00<?, ?B/s]

Processing wol_Latn...


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/37.4k [00:00<?, ?B/s]